In [2]:
import pandas as pd
import numpy as np
import yaml
from sklearn.manifold import TSNE
from sklearn.cluster import DBSCAN
from scipy.fft import fft
from scipy.stats import boxcox
from scipy.special import inv_boxcox
import matplotlib.pyplot as plt
from plotly.subplots import make_subplots
from sklearn.preprocessing import StandardScaler, OneHotEncoder, LabelEncoder, MinMaxScaler, PowerTransformer, RobustScaler
import openpyxl
import plotly.graph_objects as go
from sklearn.model_selection import train_test_split
from sklearn.metrics import classification_report, confusion_matrix, accuracy_score, recall_score,precision_score, f1_score, mean_squared_error
import xgboost as xgb
import optuna
import talib
import json
import pickle
import torch
import os
import logging

/Users/rahuladmin/GIT/Uns_SPY_Trading/venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [3]:
print(torch.backends.mps.is_available())

True


In [4]:
def load_yaml(file):
    import yaml
    with open(file, 'r') as f:
        config = yaml.safe_load(f)
    return config
    



In [5]:
config = load_yaml('../config_xgboost_reg.yaml')

In [6]:
log_dir = "logs"
os.makedirs(log_dir, exist_ok=True)
log_file = "logs_xgboost_reg.txt"
log_file_path = os.path.join(log_dir, log_file)
logging.basicConfig(
    filename=log_file_path,
    level=logging.INFO,
    format="%(asctime)s - %(levelname)s - %(message)s",
    datefmt="%Y-%m-%d %H:%M:%S"
)

logging.info("Logging started")

In [7]:
all_trading_data_dfs = []
sheet_names = ['5minData11-6-2014', '5minData12-17-2019']
for sheet in sheet_names:
    temp_df = pd.read_excel(config['all_data_excel_path'], sheet_name=sheet)
    all_trading_data_dfs.append(temp_df)
all_trading_data = pd.concat(all_trading_data_dfs, ignore_index=True)

# Load 5 min data
all_trading_data['Date'] = pd.to_datetime(all_trading_data['Date'])

In [8]:
##### Set the Date Start and End for the filtering of trading data
train_start_date = pd.to_datetime('2023-01-01')
train_end_date = pd.to_datetime('2023-05-31')
trading_data_raw = all_trading_data[(all_trading_data['Date'] >= train_start_date) & (all_trading_data['Date'] <= train_end_date)]
trading_data_raw = trading_data_raw.reset_index(drop=True)
trading_data_raw.drop(columns=['Symbol'], inplace=True)
trading_data_raw.info() 

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 7956 entries, 0 to 7955
Data columns (total 6 columns):
 #   Column  Non-Null Count  Dtype         
---  ------  --------------  -----         
 0   Date    7956 non-null   datetime64[ns]
 1   Open    7956 non-null   float64       
 2   High    7956 non-null   float64       
 3   Low     7956 non-null   float64       
 4   Close   7956 non-null   float64       
 5   Volume  7956 non-null   int64         
dtypes: datetime64[ns](1), float64(4), int64(1)
memory usage: 373.1 KB


In [9]:
fourier_lookback_window = config['fourier_lookback_window']
fourier_n_components = config['fourier_n_components']

In [10]:
def calculate_bollinger_bands(data, window_size, num_std_dev):
    rolling_mean = data['Close'].rolling(window=window_size).mean()
    rolling_std = data['Close'].rolling(window=window_size).std()
    data['BOLLBU'] = rolling_mean + (rolling_std * num_std_dev)
    data['BOLLBM'] = rolling_mean
    data['BOLLBL'] = rolling_mean - (rolling_std * num_std_dev)
    
    return data

def calculate_donchn_bands(data, window_size):
    data['DONCH_U'] = data['High'].rolling(window=window_size).max()
    data['DONCH_L'] = data['Low'].rolling(window=window_size).min()
    
    return data
    
def calculate_tchr(data):
    period = config['tchr_period']
    retracement = config['tchr_retracement']
    adj = config['tchr_adj']
    range = config['tchr_range']

    if range == 'highlow':
        data['TCHR_U'] = talib.MAX(data['High'], timeperiod=period) + adj
        data['TCHR_L'] = talib.MIN(data['Low'], timeperiod=period) - adj
    elif range == 'close':
        data['TCHR_U'] = talib.MAX(data['Close'], timeperiod=period) + adj
        data['TCHR_L'] = talib.MIN(data['Close'], timeperiod=period) - adj
    
    #calculate retracement
    if retracement == "long":
        data['TCHR'] = (data['Close'] - data['TCHR_L']) / (data['TCHR_U'] - data['TCHR_L'])
    elif retracement == "short":
        data['TCHR'] = (data['TCHR_U'] - data['Close']) / (data['TCHR_U'] - data['TCHR_L'])
    
    return data
    
def calculate_adwm(data):
    period = config['adwm_period']
    data['Previous_Close']= data['Close'].shift(1)
    data['TRH'] = data[['High', 'Previous_Close']].max(axis=1)
    data['TRL'] = data[['Low', 'Previous_Close']].min(axis=1)

    data['ADWM_AD'] = 0.0
    data.loc[data['Close'] > data['Previous_Close'], 'ADWM_AD'] = (data['Close'] - data['TRL'])
    data.loc[data['Close'] < data['Previous_Close'], 'ADWM_AD'] = (data['Close'] - data['TRH'])

    data['ADWM'] = data['ADWM_AD']

    data['ADWMMA'] = data['ADWM'].rolling(window=period).mean()

    return data

def calculate_si(row, prev_row, limit):
    if pd.isna(prev_row['Close']):
        return 0
    c = row['Close']
    c_prev = prev_row['Close']
    o = row['Open']
    o_prev = prev_row['Open']
    return (50 * ((c - c_prev) + (0.5 * (c - o)) + (0.25 * (c_prev - o_prev))) / limit)

def calculate_WASI(data):
    wasi_limit = config['wasi_limit']
    data['SI'] = data.apply(lambda row: calculate_si(row, data.shift(1).loc[row.name], wasi_limit), axis=1)
    data['WASI'] = data['SI']
    return data

def calculate_ATR(data):
    atr_period = config['atr_period']
    atr_ma = config['atr_ma']
    data['ATR'] = talib.ATR(data['High'], data['Low'], data['Close'], timeperiod=atr_period)
    data['ADJATR'] = talib.SMA(data['ATR'], timeperiod=atr_ma)
    return data


def compute_volatility_momentum(df, price_col='Close', vol_window=14, mom_window=10):
    """
    Computes rolling volatility and momentum for a given price column.

    Parameters:
        df (pd.DataFrame): DataFrame containing historical price data.
        price_col (str): Column name of the closing price.
        vol_window (int): Window size for rolling volatility calculation.
        mom_window (int): Window size for momentum calculation.

    Returns:
        pd.DataFrame: DataFrame with added 'Volatility' and 'Momentum' features.
    """

    # Ensure price column exists
    if price_col not in df.columns:
        raise ValueError(f"Column '{price_col}' not found in DataFrame")

    # 🔹 Compute Log Returns (for better volatility calculation)
    df['Log_Returns'] = np.log(df[price_col] / df[price_col].shift(1))

    # 🔹 Compute Rolling Volatility (Standard Deviation of Log Returns)
    df['Volatility'] = df['Log_Returns'].rolling(window=vol_window).std()

    # 🔹 Compute Momentum (Rate of Change in Price)
    df['Momentum'] = df[price_col].pct_change(periods=mom_window) * 100

    # 🔹 Drop NaN values from rolling computations
    #df.dropna(inplace=True)

    return df


def compute_fourier_df(value_series, n_components=10):
    fft_result = np.fft.fft(value_series)
    real = fft_result.real[:n_components]
    imag = fft_result.imag[:n_components]
    mag = np.abs(fft_result)[:n_components]

    return real, imag, mag

def get_fourier_columns():
    return [f'fourier_real_{j+2}' for j in range(fourier_n_components-1)] + [f'fourier_imag_{j+2}' for j in range(fourier_n_components-1)] + [f'fourier_mag_{j+2}' for j in range(fourier_n_components-1)]   

def transform_features(df):
    close_diff_features = config['Close_Diff_Features'].split(',')
    df[close_diff_features] = df[close_diff_features].sub(df['Close'], axis=0)
    return df    

In [11]:
def add_new_features_df(data):
    fourier_lookback_window = config['fourier_lookback_window']
    fourier_n_components = config['fourier_n_components']

    #data['Date'] = pd.to_datetime(data['Date'])
    #print(f"bolband period : {config['bolband_period']}")
    bolband_period = config['bolband_period']
    bolband_width = config['bolband_width']
    upper, middle, lower = talib.BBANDS(data['Close'], timeperiod=bolband_period, nbdevup=bolband_width, nbdevdn=bolband_width, matype=0)
    data['BOLLBU'] = upper
    data['BOLLBM'] = middle
    data['BOLLBL'] = lower
    #data = calculate_bollinger_bands(data, int(config['bolband_period']), int(config['bolband_width']))

    # Calculate DONCHN Bands
    donchn_period = config['donchn_period']
    data['DONUP'] = talib.MAX(data['High'], timeperiod=donchn_period)

    data['DONLOW'] = talib.MIN(data['Low'], timeperiod=donchn_period)

    data['DONMID'] = (data['DONLOW'] + data['DONUP']) / 2

    data['MA20'] = talib.SMA(data['Close'], timeperiod=20)

    data['MA50'] = talib.SMA(data['Close'], timeperiod=50)

    data['MA100'] = talib.SMA(data['Close'], timeperiod=100)

    data['EMA20'] = talib.EMA(data['Close'], timeperiod=20)

    # Calculate the pivot points
    data['PVPT'] = (data['High'] + data['Low'] + data['Close']) / 3
    data['PVPTR1'] = (2 * data['PVPT']) - data['Low']

    data['PVPTR2'] = data['PVPT'] + data['High'] - data['Low']

    data['PVPTR3'] = data['High'] + 2 * (data['PVPT'] - data['Low'])

    data['PVPTS1'] = (2 * data['PVPT']) - data['High']

    data['PVPTS2'] = data['PVPT'] - (data['High'] - data['Low'])

    data['PVPTS3'] = data['Low'] - 2 * (data['High'] - data['PVPT'])

    data = calculate_tchr(data)

    data = calculate_adwm(data)

    data = calculate_WASI(data)

    volume_ma_period = config['volume_ma_period']

    data['VOLMA'] = talib.SMA(data['Volume'], timeperiod=volume_ma_period)

    data = calculate_ATR(data)

    data['DayofWeek'] = data['Date'].dt.dayofweek

    data['DayofWeek'] = data['DayofWeek'].astype('category')

    data = compute_volatility_momentum(data, price_col='Close', vol_window=config['volatility_period'], mom_window=config['momentum_period'])

    data['Close_Diff'] = data['Close'].diff().fillna(0)
    data['Close_Diff_Scaled'] = data['Close_Diff']
    data['Close_Diff'] = data['Close_Diff'] * 1000

    # Add fourier columns to the df
    for i in range(fourier_n_components):
        data[f'fourier_real_{i+1}'] = np.nan
        data[f'fourier_imag_{i+1}'] = np.nan
        data[f'fourier_mag_{i+1}'] = np.nan

    features = []
    epsilon = 1e-5
    #print(f"fourier window - 1 : {fourier_lookback_window - 1}")
    for i in range(len(data)):
        if i >= fourier_lookback_window - 1:
            #print("entered point 1")
            close_window = data['Close'].iloc[i - fourier_lookback_window + 1: i + 1].values
            real, imag, mag = compute_fourier_df(close_window, n_components=fourier_n_components)

            for j in range(fourier_n_components):
                data.iloc[i, data.columns.get_loc(f'fourier_real_{j+1}')] = real[j]
                data.iloc[i, data.columns.get_loc(f'fourier_imag_{j+1}')] = imag[j]
                data.iloc[i, data.columns.get_loc(f'fourier_mag_{j+1}')] = mag[j]
                #print(data.loc[i, 'Date'])
    


    # Add the time of day feature to the trading data

    # Define max time of day in minutes
    MAX_TIME_MINUTES = 1440
    data['Minutes_Passed'] = (data['Date'].dt.hour* 60) + data['Date'].dt.minute
    print(f"number of na s : {data['Date'].isna().sum()}")
    data['TimeOfDay_Group'] = (data['Minutes_Passed'] // 5).astype('int')
    data['Sine_TimeOfDay'] = np.sin(2 * np.pi * data['TimeOfDay_Group'] / MAX_TIME_MINUTES)
    data['Cosine_TimeOfDay'] = np.cos(2 * np.pi * data['TimeOfDay_Group'] / MAX_TIME_MINUTES)
    data['Take_Profit_Level'] = (data['Close'] * config['atr_multiplier'] * data['ADJATR'])
    data['time_delta'] = data['Date'].diff().dt.total_seconds()
    data['time_delta'].fillna(data['time_delta'].median(), inplace=True)

    #print(f"Last row after adding features : ")
    #print(data.tail())
    return data


In [12]:

def calculate_label2(data):

# Define the threshold for buy and sell signals
    
    buy_powers = []
    sell_powers = []
    n=config['bars_no_to_wait']
    for i in range(len(data)):
        current_close = data.loc[i, "Close"]

        future_closes = data.loc[i+1: i+n+1, "Close"].values

        if len(future_closes) == 0:
            buy_powers.append(0)
            sell_powers.append(0)
            continue
        future_close_max = max(future_closes) 
        future_close_min = min(future_closes)
        max_high = future_close_max - current_close
        min_high = current_close - future_close_min
        max_high_idx = list(future_closes).index( future_close_max)
        min_high_idx = list(future_closes).index( future_close_min)

        if max_high_idx == (len(future_closes) - 1): #when max value is at the last of window
            buy_retr_penalty = 0
        else:
            buy_retr_penalty = future_close_max - min(future_closes[max_high_idx+1:])
        max_down_below = max(0, current_close - future_close_min)
        penalty_buy = buy_retr_penalty + max_down_below
        buy_power = max(0, max_high - penalty_buy)

        if min_high_idx == (len(future_closes) - 1): 
            sell_retr_penalty = 0
        else:
            sell_retr_penalty = max(future_closes[min_high_idx+1:]) - future_close_min
        max_up_above = max(0, future_close_max - current_close)
        penalty_sell = sell_retr_penalty + max_up_above
        sell_power = max(0, min_high - penalty_sell)

        buy_powers.append(buy_power)
        sell_powers.append(sell_power)

    data['BuyPower'] = buy_powers
    data['SellPower'] = sell_powers
        

    return data

In [13]:

def calculate_label(data):

# Define the threshold for buy and sell signals
    buy_penalties = []
    sell_penalties = []

    max_highs = []
    min_lows = []
    n=config['bars_no_to_wait']

    for i in range(len(data)):
        forward_window = data.iloc[i+1:n+i+1]

        if len(forward_window) < n:
            max_highs.append(np.nan)
            min_lows.append(np.nan)
            buy_penalties.append(np.nan)
            sell_penalties.append(np.nan)
            continue
        
        max_high = forward_window['Close'].max()
        min_low = forward_window['Close'].min()



        buy_penalty = 0
        sell_penalty = 0
        prev_close = data.iloc[i]['Close']

        for j in range(len(forward_window)):
            current_close = forward_window.iloc[j]['Close']

            if current_close < prev_close:
                buy_penalty += (prev_close - current_close)
            elif current_close > prev_close:
                sell_penalty += (current_close - prev_close)

            prev_close = current_close
        max_high = max(0, max_high - data.iloc[i]['Close'])
        min_low = max(0, data.iloc[i]['Close'] - min_low)
        max_highs.append(max_high)
        min_lows.append(min_low)
        buy_penalties.append(buy_penalty)
        sell_penalties.append(sell_penalty)

    data['Max_High_N'] = max_highs
    data['Min_Low_N'] = min_lows
    data['Buy_Penalty'] = buy_penalties
    data['Sell_Penalty'] = sell_penalties

    # Scale penalties to avoid extreme scaled values
    max_buy_penalty = max(abs(data['Buy_Penalty'].max()),1)
    max_sell_penalty = max(abs(data['Sell_Penalty'].max()),1)

    data['Scaled_Buy_Penalty'] = data['Buy_Penalty'] / max_buy_penalty * (data['Max_High_N'])
    data['Scaled_Sell_Penalty'] = data['Sell_Penalty'] / max_sell_penalty * (data['Min_Low_N'])
    
    # Reduce penalty from buy power and sell power
    data['BuyPower'] = data['Max_High_N'] - data['Scaled_Buy_Penalty']
    data['SellPower'] = data['Min_Low_N'] - data['Scaled_Sell_Penalty']

    scaler = MinMaxScaler(feature_range=(0,1))
    data['BuyPower'] = scaler.fit_transform(data[['BuyPower']])
    data['SellPower'] = scaler.fit_transform(data[['SellPower']])

    if config['label_power_transform']:
        pt = PowerTransformer(method='yeo-johnson')

        label_columns = ['BuyPower', 'SellPower']
        data[label_columns] = pt.fit_transform(data[label_columns])

        # Scale buy power and sell power to be in range 0 to 1 
        scaler = MinMaxScaler(feature_range=(0,1))
        data['BuyPower_Scaled'] = scaler.fit_transform(data[['BuyPower']])
        data['SellPower_Scaled'] = scaler.fit_transform(data[['SellPower']])

        label_scales = {'PT': pt, 'MinMax': scaler}
        with open(f'../{config['label_scales_pickle']}', 'wb') as f:
            pickle.dump(label_scales, f)
    else:
        data['BuyPower_Scaled'] = data['BuyPower']
        data['SellPower_Scaled'] = data['SellPower']

    return data




In [14]:
trading_data_features = add_new_features_df(trading_data_raw.copy())
trading_data_features = trading_data_features.dropna()
trading_data_features.reset_index(drop=True, inplace=True)

number of na s : 0


/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  data['time_delta'].fillna(data['time_delta'].median(), inplace=True)


In [15]:

trading_data_features = calculate_label2(trading_data_features)
#trading_data['Label'] = trading_data['Label'].astype('category')

In [16]:
pd.set_option("display.max_columns", None)  # Show all columns
pd.set_option("display.max_rows", None)  # Show all rows
trading_data_features.describe().T

count                           mean                  min  \
Date                 7857  2023-03-18 11:12:09.553264384  2023-01-04 11:15:00   
Open               7857.0                     404.272218               378.91   
High               7857.0                     404.536566               379.22   
Low                7857.0                      404.01024               378.76   
Close              7857.0                     404.277669             378.9097   
Volume             7857.0                  785899.957108             136615.0   
BOLLBU             7857.0                     405.500294           380.091158   
BOLLBM             7857.0                     404.231759           379.543685   
BOLLBL             7857.0                     402.963224           377.780783   
DONUP              7857.0                     405.537741               380.34   
DONLOW             7857.0                     402.872422               378.76   
DONMID             7857.0                     404.205082               379.55   
MA20               7857.0                     404.231759           379.543685   
MA50               7857.0                     404.157709            379.86122   
MA100              7857.0                      404.02865           380.520279   
EMA20              7857.0                     404.231664           379.578097   
PVPT               7857.0                     404.274825              379.075   
PVPTR1             7857.0                      404.53941              379.235   
PVPTR2             7857.0                     404.801151               379.32   
PVPTR3             7857.0                     405.065736               379.42   
PVPTS1             7857.0                     404.013084           378.643133   
PVPTS2             7857.0                     403.748499           378.376567   
PVPTS3             7857.0                     403.486758               377.24   
TCHR_U             7857.0                      412.26738               388.99   
TCHR_L             7857.0                     395.754521              372.831   
TCHR               7857.0                       0.515124             0.206016   
Previous_Close     7857.0                     404.272994             378.9097   
TRH                7857.0                     404.546181               379.22   
TRL                7857.0                     404.001671               378.76   
ADWM_AD            7857.0                       0.005082                -5.11   
ADWM               7857.0                       0.005082                -5.11   
ADWMMA             7857.0                        0.00531            -0.765421   
SI                 7857.0                        0.14614             -76.3125   
WASI               7857.0                        0.14614             -76.3125   
VOLMA              7857.0                  785161.471109             217770.1   
ATR                7857.0                       0.545209             0.215016   
ADJATR             7857.0                       0.545864             0.231332   
Log_Returns        7857.0                       0.000012            -0.013131   
Volatility         7857.0                       0.000899             0.000199   
Momentum           7857.0                       0.012544            -1.738835   
Close_Diff         7857.0                       4.674812              -5110.0   
Close_Diff_Scaled  7857.0                       0.004675                -5.11   
fourier_real_1     7857.0                   40402.865021           38052.0279   
fourier_imag_1     7857.0                            0.0                  0.0   
fourier_mag_1      7857.0                   40402.865021           38052.0279   
fourier_real_2     7857.0                      -0.371298          -166.301501   
fourier_imag_2     7857.0                       8.246097          -254.204495   
fourier_mag_2      7857.0                      82.660501             0.611365   
fourier_real_3     7857.0                      -0.2

In [17]:

trading_data_features[trading_data_features['SellPower'] > 2].shape[0]

354

In [18]:
#trading_data['Date'] = pd.to_datetime(trading_data['Date'])
fig = go.Figure(data=[go.Candlestick(x=trading_data_features['Date'], open=trading_data_features['Open'], high=trading_data_features['High'], low=trading_data_features['Low'], close=trading_data_features['Close'])])
fig.update_layout(title='CandleStick Chart SPY', xaxis_title='Date', yaxis_title='Price', xaxis_rangeslider_visible=False, yaxis=dict(fixedrange=False), xaxis=dict(type='category'))
buy_signals = trading_data_features[trading_data_features['BuyPower'] > 2]
sell_signals = trading_data_features[trading_data_features['SellPower'] > 2]
fig.add_trace(go.Scatter(x=buy_signals['Date'], y=buy_signals['Low'], mode='markers', name='Buy Signal', marker=dict(color='blue', size=10)))
fig.add_trace(go.Scatter(x=sell_signals['Date'], y=sell_signals['High'], mode='markers', name='Sell Signal', marker=dict(color='yellow', size=10)))
fig.show()

In [19]:
trading_data_transformed = transform_features(trading_data_features.copy())

In [20]:
training_features = config['training_features2'].split(',')
fourier_cols = get_fourier_columns()
training_features_upd = training_features + fourier_cols

### Going to do Robust scaling on the features that have to be scaled for training

In [21]:
rscaler = RobustScaler()
trading_data_robust_scaled = trading_data_transformed.copy()
trading_data_robust_scaled[training_features_upd] = rscaler.fit_transform(trading_data_transformed[training_features_upd])

In [22]:

label_column_names = ['BuyPower', 'SellPower']
#assert trading_features.shape[0] == trading_labels.shape[0], "Mismatch between features and labels length"
X = trading_data_robust_scaled[training_features_upd]
y = trading_data_robust_scaled[label_column_names]
X_train, X_temp, y_train, y_temp = train_test_split(X, y, test_size=0.3, random_state=43)
X_valid, X_test, y_valid, y_test = train_test_split(X_temp, y_temp, test_size=0.5, random_state=43)


In [23]:


#convert data to d matrix to use with xgb
enab_cat = True
dtrain = xgb.DMatrix(X_train, label=y_train, enable_categorical=enab_cat )
dvalid = xgb.DMatrix(X_valid, label=y_valid, enable_categorical=enab_cat)
dtest = xgb.DMatrix(X_test, label=y_test, enable_categorical=True)
dtrain_valid = xgb.DMatrix(data = pd.concat([X_train, X_valid]),label=pd.concat([y_train, y_valid]), enable_categorical=enab_cat)



In [24]:
num_boosting_rounds = 10000
##### Implement initial training of the model   
learning_rate = 0.3
starting_tree_method = 'approx'
#metric can be mlogloss, auc, merror etc
metric = 'rmse'

base_params = {
    'objective': 'reg:squarederror',
    'eval_metric': metric
}

params = {
    'learning_rate': learning_rate,
    'tree_method': starting_tree_method
}

params.update(base_params)

In [25]:
model = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, evals=[(dtrain, 'train')], early_stopping_rounds=50)

[0]	train-rmse:0.67624
[1]	train-rmse:0.62726
[2]	train-rmse:0.58625
[3]	train-rmse:0.55524
[4]	train-rmse:0.53261
[5]	train-rmse:0.51748
[6]	train-rmse:0.50009
[7]	train-rmse:0.48057
[8]	train-rmse:0.46274
[9]	train-rmse:0.45081
[10]	train-rmse:0.43690
[11]	train-rmse:0.42441
[12]	train-rmse:0.41139
[13]	train-rmse:0.40185
[14]	train-rmse:0.39341
[15]	train-rmse:0.38369
[16]	train-rmse:0.37405
[17]	train-rmse:0.36873
[18]	train-rmse:0.36031
[19]	train-rmse:0.34963
[20]	train-rmse:0.34512
[21]	train-rmse:0.33979
[22]	train-rmse:0.33261
[23]	train-rmse:0.32639
[24]	train-rmse:0.31765
[25]	train-rmse:0.31207
[26]	train-rmse:0.30249
[27]	train-rmse:0.29500
[28]	train-rmse:0.29051
[29]	train-rmse:0.28453
[30]	train-rmse:0.27979
[31]	train-rmse:0.27555
[32]	train-rmse:0.27089
[33]	train-rmse:0.26612
[34]	train-rmse:0.26316
[35]	train-rmse:0.25774
[36]	train-rmse:0.25261
[37]	train-rmse:0.24788
[38]	train-rmse:0.24394
[39]	train-rmse:0.23788
[40]	train-rmse:0.23451
[41]	train-rmse:0.23115
[4

In [26]:
##### CReate the objective function for optuna to tune tree parameters

def objective(trial):
    params = {
        'tree_method' : trial.suggest_categorical('tree_method', ['approx', 'hist']) , 
        'gamma': trial.suggest_float('gamma', 1e-2, 10),
        'max_depth': trial.suggest_int('max_depth', 3, 12),
        'min_child_weight': trial.suggest_float('min_child_weight', 1, 250),
        'subsample': trial.suggest_float('subsample', 0.1, 1.0),
        'colsample_bytree': trial.suggest_float('colsample_bytree', 0.5, 1.0),
        'lambda': trial.suggest_float('lambda', 0.1, 25), 
        'alpha': trial.suggest_float('alpha', 0.001, 10),
    }
    params.update(base_params)
    #thresholds = [trial.suggest_float(f'threshold_{i}', 0.1, 0.9) for i in ]
    pruning_callback = optuna.integration.XGBoostPruningCallback(trial, f'valid-{metric}')

    xgb_model = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, 
                          evals=[(dtrain, 'train'),(dvalid, 'valid')],
                          early_stopping_rounds=50,
                          verbose_eval=0,
                          callbacks=[pruning_callback])
    trial.set_user_attr('best_iteration', xgb_model.best_iteration)
    #xgb.XGBClassifier(**params, random_state=46, early_stopping_rounds=30, objective='multi:softprob', lambda_=config['lam'], alpha=config['alpha'], n_estimators=100)
    #xgb_model.fit(X_train, Y_train, eval_set=[(X_train, Y_train), (X_valid, Y_valid)])

    y_pred = xgb_model.predict(dvalid)
    rmse_buy = mean_squared_error(y_valid['BuyPower'], y_pred[:, 0]) ** 0.5
    rmse_sell = mean_squared_error(y_valid['SellPower'], y_pred[:, 1]) ** 0.5

    return (rmse_buy + rmse_sell) / 2

In [27]:

study = optuna.create_study(direction='minimize') # for metric auc its maximuze, and for mlogloss its minimie

study.optimize(objective, n_trials=100)

# Get the best parameters
print(f" Best parameters: {study.best_params}")
print(f" Best Accuracy: {study.best_value}")

[I 2025-02-17 22:41:06,675] A new study created in memory with name: no-name-95d89345-e5a4-44c9-a8f0-5bb1228113f6
[I 2025-02-17 22:41:06,860] Trial 0 finished with value: 0.7118111558582749 and parameters: {'tree_method': 'approx', 'gamma': 8.936385769341214, 'max_depth': 12, 'min_child_weight': 194.8892214883707, 'subsample': 0.16424016612951722, 'colsample_bytree': 0.5583647750327851, 'lambda': 18.796418770946232, 'alpha': 0.25846096365756766}. Best is trial 0 with value: 0.7118111558582749.
[I 2025-02-17 22:41:07,179] Trial 1 finished with value: 0.6905497210229445 and parameters: {'tree_method': 'approx', 'gamma': 8.054893060106966, 'max_depth': 8, 'min_child_weight': 132.37522618868013, 'subsample': 0.430515287853572, 'colsample_bytree': 0.8519544802170684, 'lambda': 12.623189341280067, 'alpha': 1.4780756939976767}. Best is trial 1 with value: 0.6905497210229445.
[I 2025-02-17 22:41:07,345] Trial 2 finished with value: 0.6760060418513125 and parameters: {'tree_method': 'hist', 'ga

 Best parameters: {'tree_method': 'hist', 'gamma': 0.025219915561446093, 'max_depth': 6, 'min_child_weight': 14.187625644839457, 'subsample': 0.8364708272036467, 'colsample_bytree': 0.5669640726326155, 'lambda': 1.7888339324332256, 'alpha': 1.8648113513213536}
 Best Accuracy: 0.457156836872891


In [28]:
best_params = study.best_params
best_params

{'tree_method': 'hist',
 'gamma': 0.025219915561446093,
 'max_depth': 6,
 'min_child_weight': 14.187625644839457,
 'subsample': 0.8364708272036467,
 'colsample_bytree': 0.5669640726326155,
 'lambda': 1.7888339324332256,
 'alpha': 1.8648113513213536}

In [88]:
low_learning_rate = 0.08

params = {}
params.update(base_params)
params.update(study.best_params)
params['learning_rate'] = low_learning_rate

model_stage2 = xgb.train(params=params, dtrain=dtrain, num_boost_round=num_boosting_rounds, 
                         evals=[(dtrain, 'train'), (dvalid, 'valid')], 
                         early_stopping_rounds=50,
                         verbose_eval=0)

In [89]:
model_stage2.best_iteration # got the best iteration from stage 2 training

1614

In [90]:
model_final = xgb.train(params=params, dtrain=dtrain_valid,
                        num_boost_round = model_stage2.best_iteration,
                        verbose_eval=0)

In [91]:
#model_path = f'../{config['model_save_name']}'
#model_final.save_model(model_path)

In [92]:
y_pred_test = model_final.predict(dtest)

y_pred_buy = y_pred_test[:, 0]

y_pred_sell = y_pred_test[:, 1]

metrics = {
    "RMSE (Buy Power)": mean_squared_error( y_test['BuyPower'], y_pred_buy),
    "RMSE (Sell Power)": mean_squared_error(y_test['SellPower'], y_pred_sell),
}

df_metrics = pd.DataFrame(metrics.items(), columns=["Metric", "Value"])

print(df_metrics)


              Metric     Value
0   RMSE (Buy Power)  0.182027
1  RMSE (Sell Power)  0.198493


In [93]:
new_data_start_date = pd.to_datetime('2023-06-01')
new_data_end_date = pd.to_datetime('2023-09-30')
new_data = all_trading_data[(all_trading_data['Date'] >= new_data_start_date) & (all_trading_data['Date'] <= new_data_end_date)]
new_data = new_data.reset_index(drop=True)

In [94]:
new_data.shape

(6517, 7)

In [95]:
bolband_period = config['bolband_period']
donchn_period = config['donchn_period']
max_MA_period = 100
max_EMA_period = 20
tchr_period = config['tchr_period']
adwm_period = config['adwm_period']
atr_period = config['atr_period']
volume_ma_period = config['volume_ma_period']
print(f" Fourier window : {fourier_lookback_window}")
max_window = max(bolband_period, 
                 donchn_period, 
                 max_MA_period, 
                 max_EMA_period,
                 tchr_period,
                 adwm_period,
                 atr_period,
                 volume_ma_period, fourier_lookback_window)
print(f"Max window : {max_window}")


 Fourier window : 100
Max window : 100


In [96]:
def process_data(raw_data, scaler):

    trading_signals = pd.DataFrame(columns=['Date','High', 'Low', 'Open', 'Close', 'BuyPower', 'SellPower', 'Signal', 'Take_Profit_Level'])                   
    # This is the dataframe to which we will be adding the rows live
    historical_data = pd.DataFrame(columns=['Date','High', 'Low', 'Open', 'Close', 'Volume'])
    numeric_columns = ['High', 'Low', 'Open', 'Close', 'Volume'] 
    historical_data[numeric_columns] = historical_data[numeric_columns].apply(pd.to_numeric)
    predictions = []
    for index,row in raw_data.iterrows():

        if index % 100 == 0:
            logging.info(f'Index : {index}')
        new_row = pd.DataFrame({'Date': [row['Date']], 'High': [row['High']], 'Low': [row['Low']], 'Open': [row['Open']], 'Close': [row['Close']], 'Volume': [row['Volume']]})
        signal_row = pd.DataFrame({'Date': [row['Date']], 'High': [row['High']], 'Low': [row['Low']], 'Open': [row['Open']], 'Close': [row['Close']], 'Signal': ['N']})
        trading_signals = pd.concat([trading_signals, signal_row], ignore_index=True)
        historical_data = pd.concat([historical_data, new_row], ignore_index=True)
        historical_data['Volume'] = historical_data['Volume'].astype(int)
        #if len(historical_data) > max_window:
        #    historical_data = historical_data.iloc[-max_window:].reset_index(drop=True)
        if len(historical_data) > max_window:
            #print("Hist data length : ", len(historical_data))
            updated_data = add_new_features_df(historical_data)
            historical_data = historical_data.iloc[-max_window:].reset_index(drop=True)
            #print("Updated data length : ", len(updated_data))
            data_transformed = transform_features(updated_data)
            #print("Data transformed length : ", len(data_transformed))
            #data_transformed = data_transformed.dropna() 
            #data_transformed.reset_index(drop=True, inplace=True)
            inf_features = data_transformed.iloc[-max_window:].reset_index(drop=True)
            #print(f"inf_features shape : {inf_features.shape} and training features : {training_features_upd}")
            #print(inf_features.tail())
            inf_features[training_features_upd] = scaler.transform(inf_features[training_features_upd])
            last_row_features = inf_features.iloc[[-1]]
            last_row_features = last_row_features[training_features_upd]
            if last_row_features.isna().any().any():
                print(f'The inference row at index : {index} contains na')
                print(historical_data[['Volume']].tail())
                break
                continue
        
            last_row_dm = xgb.DMatrix(last_row_features, enable_categorical=True)
            prediction = model_final.predict(last_row_dm)
 
            buy_power, sell_power = prediction[0]
            trading_signals.loc[trading_signals.index[-1], 'BuyPower'] = buy_power
            trading_signals.loc[trading_signals.index[-1], 'SellPower'] = sell_power
            trading_signals.loc[trading_signals.index[-1], 'Take_Profit_Level'] = updated_data['Take_Profit_Level'].iloc[-1]
        
    return trading_signals
    

In [97]:
def calculate_trade(trading_signals):
    trade_positions = []
    #trade_enter_buy = config['trade_enter_buy']
    #trade_enter_sell = config['trade_enter_sell']
    trade_enter_buy = 0.7
    trade_enter_sell = 0.7
    trades = []
    balance = 0
    profit_amount = 10
    profit_count = 0
    loss_count = 0
    buy_count = 0
    sell_count = 0
    loss_amount = profit_amount * config['risk']
    positions = pd.DataFrame(columns=['Entry', 'EntryDate', 'Exit', 'ExitDate', 'Profit', 'Type'])
                    
    for index,row in trading_signals.iterrows():
        buy_power = row['BuyPower']
        sell_power = row['SellPower']
        #print(f'Buy Power : {buy_power}, Sell Power : {sell_power}')

        #predicted_class_index = np.argmax(prob_prediction, axis=1)          #predictions.append(prediction[0])
        for trade in trades:
            if (trade['Type'] == 'B' and row['High'] >= trade['TakeProfit']) or (trade['Type'] == 'S' and row['Low'] <= trade['TakeProfit']):
                trade['Active'] = 'N'
                balance += (trade['Profit'] * profit_amount)
                profit_count += 1
                print(f"Profit, New Balance : {balance}")
                
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
            elif (trade['Type'] == 'B' and row['Low'] <= trade['StopLoss']) or (trade['Type'] == 'S' and row['High'] >= trade['StopLoss']):
                trade['Active'] = 'N'
                balance -= (trade['Profit'] * loss_amount)
                loss_count += 1
                print(f"Loss, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
        
        
        if len(trades) == 0:
            if buy_power > sell_power and buy_power > trade_enter_buy:
                take_profit = row['Take_Profit_Level'] 
                trades.append({"Type": "B", 
                            "TakeProfit": row['Close'] + take_profit,
                            "StopLoss": row['Close'] - (take_profit * config['risk']),
                            "Profit": take_profit,
                            "Active": "Y",
                            'Entry': row['Close'],
                            'EntryDate': row['Date']
                            })
                buy_count += 1
            elif sell_power > buy_power and sell_power > trade_enter_sell:
                take_profit = row['Take_Profit_Level'] 
                trades.append({"Type": "S", 
                            "TakeProfit": row['Close'] - take_profit,
                            "Profit": take_profit,
                            "StopLoss": row['Close'] + (take_profit * config['risk']),
                            "Active": "Y",
                            'Entry': row['Close'],
                            'EntryDate': row['Date']
                            })
                sell_count += 1
        else:
            if buy_power > sell_power and buy_power > trade_enter_buy and trades[0]['Type'] == 'S':
                trade['Active'] = 'N'
                profit = (trade['Entry'] - row['Close']) * profit_amount
                balance += profit 
                if profit < 0:
                    loss_count += 1
                    print(f"Loss, New Balance : {balance}")
                else:
                    profit_count += 1
                    print(f"Profit, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True] if profit > 0 else [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)

            elif sell_power > buy_power and sell_power > trade_enter_sell and trades[0]['Type'] == 'B':
                trade['Active'] = 'N'
                profit = (row['Close'] - trade['Entry']) * profit_amount
                balance += profit
                if profit < 0:
                    loss_count += 1
                    print(f"Loss, New Balance : {balance}")
                else:
                    profit_count += 1
                    print(f"Profit, New Balance : {balance}")
                pos_row = pd.DataFrame({'Entry': [trade['Entry']], 'EntryDate': [trade['EntryDate']], 'Exit': [row['Close']], 'ExitDate': [row['Date']] , 'Profit': [True] if profit > 0 else [False], 'Type': [trade['Type']]})
                positions = pd.concat([positions, pos_row], ignore_index=True)
            
        # Filter out all trades that are not active
        trades = [trade for trade in trades if trade['Active'] == 'Y']
        
        
    print(f"Final Balance : {balance} \n Profit count : {profit_count} \n Loss count : {loss_count}")
    print(f"Buy count : {buy_count} \n Sell count : {sell_count}")
    
    return positions

            

        
    

In [98]:
new_data.isna().any(axis=1).sum()

np.int64(0)

In [99]:
print(volume_ma_period)

10


In [100]:
new_data.head()

Date Symbol    Open    High     Low     Close   Volume
0 2023-06-01 09:30:00    SPY  418.09  418.28  417.18  417.2200  1516077
1 2023-06-01 09:35:00    SPY  417.22  417.67  417.03  417.6600  1344596
2 2023-06-01 09:40:00    SPY  417.66  417.68  417.12  417.3200   828877
3 2023-06-01 09:45:00    SPY  417.32  417.34  416.92  417.1800   872652
4 2023-06-01 09:50:00    SPY  417.18  417.31  416.79  417.0792  1000157

In [101]:
tr_signals = process_data(new_data, rscaler)

number of na s : 0
number of na s : 0
number of na s : 0

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/2699226810.py:15: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/2699226810.py:16: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in


number of na s : 0
number of na s : 0
number of na s : 0
number of na s : 0


/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doi

number of na s : 0
number of na s : 0
number of na s : 0
number of na s : 0
number of na s : 0


...

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doi

number of na s : 0
number of na s : 0
number of na s : 0
number of na s : 0
number of na s : 0


/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doi

number of na s : 0
number of na s : 0
number of na s : 0


/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.



/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275656416.py:101: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doi

In [102]:
tr_signals

Date      High       Low      Open     Close  BuyPower  \
0    2023-06-01 09:30:00  418.2800  417.1800  418.0900  417.2200       NaN   
1    2023-06-01 09:35:00  417.6700  417.0300  417.2200  417.6600       NaN   
2    2023-06-01 09:40:00  417.6800  417.1200  417.6600  417.3200       NaN   
3    2023-06-01 09:45:00  417.3400  416.9200  417.3200  417.1800       NaN   
4    2023-06-01 09:50:00  417.3100  416.7900  417.1800  417.0792       NaN   
5    2023-06-01 09:55:00  417.3900  416.8700  417.0700  417.2000       NaN   
6    2023-06-01 10:00:00  418.0800  417.2100  417.2700  417.8650       NaN   
7    2023-06-01 10:05:00  418.2847  417.8492  417.8700  418.0700       NaN   
8    2023-06-01 10:10:00  418.5600  418.0300  418.1000  418.5200       NaN   
9    2023-06-01 10:15:00  418.7500  417.8800  418.5150  418.0100       NaN   
10   2023-06-01 10:20:00  418.0700  417.5100  418.0100  417.6075       NaN   
11   2023-06-01 10:25:00  418.1100  417.4101  417.6192  418.0100       NaN   
12   2023-06-01 10:30:00  418.1600  417.8700  418.0100  418.0500       NaN   
13   2023-06-01 10:35:00  418.4800  417.9900  418.0800  418.4150       NaN   
14   2023-06-01 10:40:00  419.2800  418.3597  418.4100  419.2000       NaN   
15   2023-06-01 10:45:00  419.7500  418.9800  419.1900  419.2700       NaN   
16   2023-06-01 10:50:00  419.5200  419.2250  419.3000  419.4650       NaN   
17   2023-06-01 10:55:00  419.5600  419.2650  419.4700  419.3700       NaN   
18   2023-06-01 11:00:00  419.5100  419.1800  419.3800  419.4200       NaN   
19   2023-06-01 11:05:00  419.5900  419.2665  419.4300  419.3400       NaN   
20   2023-06-01 11:10:00  419.9000  419.2500  419.3300  419.8000       NaN   
21   2023-06-01 11:15:00  420.3100  419.8100  419.8100  419.9300       NaN   
22   2023-06-01 11:20:00  420.1100  419.6900  419.9300  420.1000       NaN   
23   2023-06-01 11:25:00  420.3100  419.9700  420.1018  420.1700       NaN   
24   2023-06-01 11:30:00  420.5000  420.0900  420.1800  420.3600       NaN   
25   2023-06-01 11:35:00  420.5800  420.1800  420.3700  420.2384       NaN   
26   2023-06-01 11:40:00  420.7100  420.2050  420.2300  420.5400       NaN   
27   2023-06-01 11:45:00  420.8300  420.5100  420.5500  420.7913       NaN   
28   2023-06-01 11:50:00  421.0600  420.7100  420.8000  420.8700       NaN   
29   2023-06-01 11:55:00  421.0942  420.7800  420.8899  421.0550       NaN   
30   2023-06-01 12:00:00  421.5100  421.0600  421.0600  421.2300       NaN   
31   2023-06-01 12:05:00  421.3500  421.0900  421.2300  421.2600       NaN   
32   2023-06-01 12:10:00  421.4000  421.1600  421.2523  421.3000       NaN   
33   2023-06-01 12:15:00  421.5600  421.1400  421.3100  421.5000       NaN   
34   2023-06-01 12:20:00  421.8450  421.4510  421.5100  421.6550       NaN   
35   2023-06-01 12:25:00  421.7400  421.5800  421.6500  421.7400       NaN   
36   2023-06-01 12:30:00  421.8100  421.5400  421.7500  421.6000       NaN   
37   2023-06-01 12:35:00  421.7300  421.5400  421.6100  421.6600       NaN   
38   2023-06-01 12:40:00  421.7000  421.4900  421.6700  421.5100       NaN   
39   2023-06-01 12:45:00  421.6300  421.2625  421.5099  421.6200       NaN   
40   2023-06-01 12:50:00  421.6800  421.5000  421.6300  421.6400       NaN   
41   2023-06-01 12:55:00  421.7700  421.5400  421.6500  421.6620       NaN   
42   2023-06-01 13:00:00  421.7700  421.5100  421.6700  421.5700       NaN   
43   2023-06-01 13:05:00  421.7700  421.4600  421.5750  421.4700       NaN   
44   2023-06-01 13:10:00  421.7600  421.4200  421.4700  421.7565       NaN   
45   2023-06-01 13:15:00  421.7600  421.5631  421.7599  421.6350       NaN   
46   2023-06-01 13:20:00  421.9399  421.3500  421.6200  421.5050       NaN   
47   2023-06-01 13:25:00  421.5600  421.2700  421.5100  421.5000       NaN   
48   2023-06-01 13:30:00  421.5500  421.3100  421.5000  421.4791       NaN   
49   2023-06-01 13:35:00  421.5750  421.3896  421.4800  421.4700       NaN   
50   2023-06-01 13:40:00  421.5900  421.33

In [103]:
positions_df = calculate_trade(tr_signals.copy())
#tr_signals.tail()

Loss, New Balance : -14.25656254911276
Loss, New Balance : -16.20756254911244
Loss, New Balance : -22.508562549112142
Loss, New Balance : -30.976562549111875
Loss, New Balance : -33.62656254911174
Profit, New Balance : -23.326562549111443
Profit, New Balance : 3.2457364727660547
Profit, New Balance : 18.396736472766236
Profit, New Balance : 20.096736472766395
Profit, New Balance : 48.31173647276597
Loss, New Balance : 47.51173647276613
Profit, New Balance : 49.56173647276654
Loss, New Balance : 38.8210381455901
Loss, New Balance : 36.07103814559033
Profit, New Balance : 68.77326262343607
Profit, New Balance : 101.40960979658644
Loss, New Balance : 85.86889643835326
Profit, New Balance : 86.41889643835276
Profit, New Balance : 94.11889643835258
Profit, New Balance : 95.51889643835244
Profit, New Balance : 99.4188964383523
Loss, New Balance : 59.91966617737762
Loss, New Balance : 42.10027621576514
Loss, New Balance : 20.741526275332866
Loss, New Balance : 2.5815391260342757
Loss, New Bal

/var/folders/ns/6tgyd_dx5lq_3chvzvfdm1sr0000gp/T/ipykernel_17809/4275680926.py:38: FutureWarning:

The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.



In [104]:
def compute_trade_signal(row):
    if row['BuyPower'] > config['trade_enter_buy'] and row['BuyPower'] > row['SellPower']:
        return 'B'
    elif row['SellPower'] > config['trade_enter_sell'] and row['SellPower'] > row['BuyPower']:
        return 'S'
    else:
        return 'N'
    
tr_signals['Signal'] = tr_signals.apply(compute_trade_signal, axis=1)

In [ ]:
buy_signals = tr_signals[tr_signals['Signal'] == 'B']
sell_signals = tr_signals[tr_signals['Signal']== 'S']
#trading_data['Date'] = pd.to_datetime(trading_data['Date'])
fig = make_subplots(rows=2, cols=1, shared_xaxes=True, 
                    row_heights=[0.7, 0.3], vertical_spacing=0.1,
                    subplot_titles=("CandleStick Chart", "Buy/Sell Signals"))
fig.add_trace(
    go.Candlestick(
        x=tr_signals['Date'], 
        open=tr_signals['Open'], 
        high=tr_signals['High'], 
        low=tr_signals['Low'], 
        close=tr_signals['Close'],
        name='OHLC'
        ), row=1, col=1
)
'''
fig.add_trace(
    go.Scatter(
        x=buy_signals['Date'], 
        y=buy_signals['Low'], 
        mode='markers', 
        name='Buy Signal', 
        marker=dict(color='blue', size=10)))

fig.add_trace(
    go.Scatter(
        x=sell_signals['Date'], 
        y=sell_signals['High'], 
        mode='markers', 
        name='Sell Signal', 
        marker=dict(color='yellow', size=10)))
'''
for index, row in positions_df.iterrows():
    if row['Type'] == 'B':
        entry_symbol = 'triangle-up'
        entry_color = 'blue'
        exit_symbol = 'triangle-down'
        exit_color ='green' if row['Profit'] else 'red'
    elif row['Type'] == 'S':
        entry_symbol = 'triangle-down'
        entry_color = 'yellow'
        exit_symbol = 'triangle-up'
        exit_color = 'green' if row['Profit'] else 'red'
    
    fig.add_trace(
        go.Scatter(
            x=[row['EntryDate']],
            y=[row['Entry']],
            mode='markers',
            marker=dict(symbol=entry_symbol, size=10, color=entry_color),
            name=f'Entry {row['Type']}'
        ))
    
    fig.add_trace(
        go.Scatter(
            x=[row['ExitDate']],
            y=[row['Exit']],
            mode='markers',
            marker=dict(symbol=exit_symbol, size=10, color=exit_color),
            name=f'Exit {row["Type"]}'
        ))
    
fig.add_trace(
    go.Scatter(
        x=tr_signals['Date'],
        y=tr_signals['BuyPower'],
        mode='lines',
        name='Buy Signal',
        line=dict(color='green', width=2)
    ), row=2, col=1
)

fig.add_trace(
    go.Scatter(
        x=tr_signals['Date'],
        y=tr_signals['SellPower'],
        mode='lines',
        name='Sell Signal',
        line=dict(color='red', width=2)
    ), row=2, col=1
)
   

fig.update_layout(
    title='CandleStick chart with Buy Sell Signals',
    xaxis=dict(type="date", 
               rangebreaks=[
                   dict(bounds=["sat", "mon"]),
                   dict(bounds=[16,9.5], pattern='hour')
               ]              
            ),
    xaxis_rangeslider_visible=False,
    height=600,
    hovermode='x unified'
)



fig.update_xaxes(matches='x')

fig.show()